# Getting data into the right format

In order to use `SegTraQ`, you first need to get your data into a `SpatialData` object. While `spatialdata_io` has a lot of readers for different technologies, the constantly evolving landscape of segmentation methods makes it difficult to provide up-to-date, generalizable readers. To facilitate the process of getting your data into the correct format, we provide examples for some segmentation methods.

To follow along with this tutorial, you can download the data from [here](https://oc.embl.de/index.php/s/1JyN4Qvk4mw0T5J).

## Proseg 3

Proseg 3 already provides a `SpatialData` object as output, which can be read in easily.

In [1]:
%load_ext autoreload
%autoreload 2

import spatialdata as sd

sdata = sd.read_zarr("../../data/proseg_output_v3/proseg-output.zarr/")
sdata

/g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/.venv/lib/python3.13/site-packages/dask/dataframe/__init__.py:31: FutureWarning: The legacy Dask DataFrame implementation is deprecated and will be removed in a future version. Set the configuration option `dataframe.query-planning` to `True` or None to enable the new Dask Dataframe implementation and silence this warning.
  warnings.warn(
/g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/.venv/lib/python3.13/site-packages/xarray_schema/__init__.py:1: UserWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html. The pkg_resources package is slated for removal as early as 2025-11-30. Refrain from using this package or pin to Setuptools<81.
  from pkg_resources import DistributionNotFound, get_distribution
/g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/.venv/lib/python3.13/site-packages/spatialdata/_core/query/relational_query.py:532: Fut

SpatialData object, with associated Zarr store: /g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/data/proseg_output_v3/proseg-output.zarr
├── Points
│     └── 'transcripts': DataFrame with shape: (<Delayed>, 10) (3D points)
├── Shapes
│     └── 'cell_boundaries': GeoDataFrame shape: (17956, 2) (2D shapes)
└── Tables
      └── 'table': AnnData (17956, 5095)
with coordinate systems:
    ▸ 'global', with elements:
        transcripts (Points), cell_boundaries (Shapes)

Note that this object only contains one `cell_boundaries` layer in the shapes. To make full use of the 3D metrics of `SegTraQ`, we can also read in the segmentations at different z layers.

In [2]:
import gzip
import shutil
import warnings
from pathlib import Path

import geopandas as gpd

warnings.filterwarnings(
    "ignore",
    message="GeoSeries.notna.*previously returned False.*",
    category=UserWarning,
)


# adding the shapes for the different z layers
def decompress_geojson(gz_path: Path) -> Path:
    if gz_path.suffix == ".gz":
        json_path = gz_path.with_suffix("")  # strip .gz
        if not json_path.exists():
            with gzip.open(gz_path, "rt") as f_in, open(json_path, "w") as f_out:
                shutil.copyfileobj(f_in, f_out)
        return json_path
    return gz_path


path = Path("../../data/proseg_output_v3/")

# reading the polygons
polygons_gdf = gpd.read_file(decompress_geojson(path / "cell-polygons-layers.geojson.gz"))

# Polygon layers for multiple z stacks
for z in sorted(polygons_gdf["layer"].unique()):
    # select the current layer
    layer_gdf = polygons_gdf[polygons_gdf["layer"] == z]
    # filter out empty or missing geometries
    layer_gdf = layer_gdf[~layer_gdf.geometry.is_empty & layer_gdf.geometry.notna()]
    # putting everything into a spatialdata-compatible format
    layer_shapes = layer_gdf.set_index("cell")["geometry"].to_frame().copy()
    layer_shapes.index.name = "label_id"
    layer_shapes["cell_id"] = layer_shapes.index
    sdata.shapes[f"cell_boundaries_z{int(z)}"] = sd.models.ShapesModel.parse(layer_shapes)

sdata

SpatialData object, with associated Zarr store: /g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/data/proseg_output_v3/proseg-output.zarr
├── Points
│     └── 'transcripts': DataFrame with shape: (<Delayed>, 10) (3D points)
├── Shapes
│     ├── 'cell_boundaries': GeoDataFrame shape: (17956, 2) (2D shapes)
│     ├── 'cell_boundaries_z0': GeoDataFrame shape: (17638, 2) (2D shapes)
│     ├── 'cell_boundaries_z1': GeoDataFrame shape: (17823, 2) (2D shapes)
│     ├── 'cell_boundaries_z2': GeoDataFrame shape: (17822, 2) (2D shapes)
│     └── 'cell_boundaries_z3': GeoDataFrame shape: (16450, 2) (2D shapes)
└── Tables
      └── 'table': AnnData (17956, 5095)
with coordinate systems:
    ▸ 'global', with elements:
        transcripts (Points), cell_boundaries (Shapes), cell_boundaries_z0 (Shapes), cell_boundaries_z1 (Shapes), cell_boundaries_z2 (Shapes), cell_boundaries_z3 (Shapes)
with the following elements not in the Zarr store:
    ▸ cell_boundaries_z2 (Shapes)
    ▸ cell_b

Some metrics in `SegTraQ` also depend on a nuclear segmentation mask. Here, we read in the nuclear segmentation provided by Xenium.

In [3]:
# adding nucleus boundaries from Xenium
import numpy as np
import pandas as pd
from shapely.geometry import MultiPolygon, Polygon
from shapely.validation import make_valid


# Convert a vertex table (one row per boundary vertex) into a GeoDataFrame of cell polygons.
def build_cell_polygons_from_vertices(
    df: pd.DataFrame,
    id_col: str = "label_id",
    x_col: str = "vertex_x",
    y_col: str = "vertex_y",
    keep_attrs=("cell_id",),
    drop_closed_duplicate: bool = True,
    fix_invalid: bool = True,
) -> gpd.GeoDataFrame:
    rows = []
    geometries = []

    for label_id, group in df.groupby(id_col, sort=False):
        xs = group[x_col].to_numpy()
        ys = group[y_col].to_numpy()

        # Drop last duplicate closing point if present
        if drop_closed_duplicate and len(xs) >= 2 and xs[0] == xs[-1] and ys[0] == ys[-1]:
            xs = xs[:-1]
            ys = ys[:-1]

        if len(xs) < 3:
            continue  # not enough points to form a polygon

        poly = Polygon(np.column_stack([xs, ys]))

        # Repair invalid polygons
        if fix_invalid and not poly.is_valid:
            poly = make_valid(poly)
            if poly.geom_type == "GeometryCollection":
                polys = [p for p in poly.geoms if p.geom_type in ("Polygon", "MultiPolygon")]
                if not polys:
                    continue
                poly = polys[0] if len(polys) == 1 else MultiPolygon(polys)

        if poly.is_empty:
            continue

        row = {id_col: int(label_id) if pd.notna(label_id) else None}
        for attr in keep_attrs:
            if attr in group.columns:
                row[attr] = group[attr].iloc[0]

        rows.append(row)
        geometries.append(poly)

    gdf = gpd.GeoDataFrame(rows, geometry=geometries)
    gdf.set_index(id_col, inplace=True)
    return gdf


nucleus_shapes = pd.read_parquet("../../data/nucleus_boundaries.parquet")
nucleus_shapes = build_cell_polygons_from_vertices(nucleus_shapes)
sdata.shapes["nucleus_boundaries"] = sd.models.ShapesModel.parse(nucleus_shapes)

# we also need to add the correct transformations to our new shapes
cell_shape_transformation = sd.transformations.get_transformation(sdata.shapes["cell_boundaries"])
sd.transformations.set_transformation(sdata.shapes["nucleus_boundaries"], cell_shape_transformation)

sdata

SpatialData object, with associated Zarr store: /g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/data/proseg_output_v3/proseg-output.zarr
├── Points
│     └── 'transcripts': DataFrame with shape: (<Delayed>, 10) (3D points)
├── Shapes
│     ├── 'cell_boundaries': GeoDataFrame shape: (17956, 2) (2D shapes)
│     ├── 'cell_boundaries_z0': GeoDataFrame shape: (17638, 2) (2D shapes)
│     ├── 'cell_boundaries_z1': GeoDataFrame shape: (17823, 2) (2D shapes)
│     ├── 'cell_boundaries_z2': GeoDataFrame shape: (17822, 2) (2D shapes)
│     ├── 'cell_boundaries_z3': GeoDataFrame shape: (16450, 2) (2D shapes)
│     └── 'nucleus_boundaries': GeoDataFrame shape: (18608, 2) (2D shapes)
└── Tables
      └── 'table': AnnData (17956, 5095)
with coordinate systems:
    ▸ 'global', with elements:
        transcripts (Points), cell_boundaries (Shapes), cell_boundaries_z0 (Shapes), cell_boundaries_z1 (Shapes), cell_boundaries_z2 (Shapes), cell_boundaries_z3 (Shapes), nucleus_boundaries (S

Finally, we can read these into SegTraQ. Don't worry if you do not know all of these parameters up front, you can start by simply passing an `sdata` object into the function and it will tell you exactly which parameters need to be set.

In [11]:
import segtraq

segtraq.SegTraQ(
    sdata,
    points_cell_id_key="assignment",
    points_background_id=None,
    points_gene_key="gene",
    tables_area_volume_key="volume",
    shapes_cell_id_key="cell",
    tables_cell_id_key="cell",
    images_key=None,
    tables_x_key="centroid_x",
    tables_y_key="centroid_y",
)

## Xenium

For Xenium data, we can make use of the functions from `spatialdata_io`. 

In [12]:
import spatialdata_io  # noqa

sdata = spatialdata_io.xenium("/g/huber/projects/CODEX/segtraq/data/xenium_4_0_testdata")
sdata

/tmp/ipykernel_27762/1929328261.py:3: DeprecationWarning: The default value of `cells_as_circles` will change to `False` in the next release. Please pass `True` explicitly to maintain the current behavior.
  sdata = spatialdata_io.xenium("/g/huber/projects/CODEX/segtraq/data/xenium_4_0_testdata")
/g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/.venv/lib/python3.13/site-packages/spatialdata_io/_utils.py:59: UserWarning: The "cell_id" column in the cells metadata table does not match the "cell_id" column in the annotation table. This could be due to trying to read a new version that is not supported yet. Please report this issue.
  return f(*args, **kwargs)
/g/huber/users/meyerben/notebooks/spatial_transcriptomics/SegTraQ/.venv/lib/python3.13/site-packages/spatialdata_io/_utils.py:59: UserWarning: The cell_id column in the cell_labels_table does not match the cell_id column derived from the cell labels data. This could be due to trying to read a new version that is not 

SpatialData object
├── Images
│     └── 'morphology_focus': DataTree[cyx] (12, 6915, 2963), (12, 3457, 1481), (12, 1728, 740), (12, 864, 370), (12, 432, 185)
├── Labels
│     ├── 'cell_labels': DataTree[yx] (6915, 2963), (3457, 1481), (1728, 740), (864, 370), (432, 185)
│     └── 'nucleus_labels': DataTree[yx] (6915, 2963), (3457, 1481), (1728, 740), (864, 370), (432, 185)
├── Points
│     └── 'transcripts': DataFrame with shape: (<Delayed>, 13) (3D points)
├── Shapes
│     ├── 'cell_boundaries': GeoDataFrame shape: (358, 1) (2D shapes)
│     ├── 'cell_circles': GeoDataFrame shape: (358, 2) (2D shapes)
│     └── 'nucleus_boundaries': GeoDataFrame shape: (356, 1) (2D shapes)
└── Tables
      └── 'table': AnnData (358, 405)
with coordinate systems:
    ▸ 'global', with elements:
        morphology_focus (Images), cell_labels (Labels), nucleus_labels (Labels), transcripts (Points), cell_boundaries (Shapes), cell_circles (Shapes), nucleus_boundaries (Shapes)

You can put this object into the `SegTraQ` constructor like this.

In [14]:
st = segtraq.SegTraQ(
    sdata, shapes_cell_id_key=None, nucleus_shapes_cell_id_key=None, tables_x_key=None, tables_y_key=None
)